In [42]:
"""
TripsLayer
==========

Plot of a single vehicle trip within San Francisco, fading in from the origin.

Adapted from a deck.gl documentation example.
"""

import pydeck as pdk
import pandas as pd

# TRIPS_LAYER_DATA = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/website/sf.trips.json"  # noqa

# df = pd.read_json(TRIPS_LAYER_DATA)

# --- 1. Load Data ---
DATA_URL = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/examples/trips/trips-v7.json"

print("Loading data...")
df = pd.read_json(DATA_URL)

# df["coordinates"] = df["waypoints"].apply(lambda f: [item["coordinates"] for item in f])
# df["timestamps"] = df["waypoints"].apply(lambda f: [item["timestamp"] - 1554772579000 for item in f])

df.drop(["vendor"], axis=1, inplace=True)

layer = pdk.Layer(
    "TripsLayer",
    df,
    get_path="path",
    get_timestamps="timestamps",
    get_color=[253, 128, 93],
    opacity=0.8,
    width_min_pixels=5,
    rounded=True,
    trail_length=600,
    current_time=1095,
)

view_state = pdk.ViewState(latitude=40.74944358256174, longitude=-73.99122131549699, zoom=11, bearing=0, pitch=45)

# Render
r = pdk.Deck(layers=[layer], initial_view_state=view_state)
# with map_output:
display(r.show())

# ui = widgets.VBox([
#     map_output
# ])
# display(ui)

Loading data...


In [46]:
import pandas as pd
import json

# --- 1. Load Data ---
# Trips Data
TRIPS_URL = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/examples/trips/trips-v7.json"
print("Loading trips data...")
df_trips = pd.read_json(TRIPS_URL)
trips_json = df_trips.to_dict(orient='records')

# Buildings Data
BUILDINGS_URL = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/examples/trips/buildings.json"
print("Loading buildings data...")
df_buildings = pd.read_json(BUILDINGS_URL)
buildings_json = df_buildings.to_dict(orient='records')

# --- 2. Define the HTML Template with Theme & Lighting ---

html_template = f"""
<!DOCTYPE html>
<html>
  <head>
    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
    <title>Deck.gl Trips - NYC Theme</title>
    
    <script src="https://unpkg.com/deck.gl@^8.8.0/dist.min.js"></script>
    <script src="https://unpkg.com/mapbox-gl@^2.0.0/dist/mapbox-gl.js"></script>
    <link href="https://unpkg.com/mapbox-gl@^2.0.0/dist/mapbox-gl.css" rel="stylesheet" />
    
    <style>
      body {{ margin: 0; padding: 0; background: #000; }}
      #container {{ width: 100vw; height: 100vh; position: relative; }}
    </style>
  </head>
  <body>
    <div id="container"></div>
    
    <script type="text/javascript">
      // 1. Ingest Data
      const TRIPS_DATA = {json.dumps(trips_json)};
      const BUILDINGS_DATA = {json.dumps(buildings_json)};

      // 2. Setup Lighting & Theme
      const {{AmbientLight, PointLight, LightingEffect}} = deck;

      // Create lights to simulate the 'city at night' look
      const ambientLight = new AmbientLight({{
        color: [255, 255, 255],
        intensity: 1.0
      }});

      const pointLight = new PointLight({{
        color: [255, 255, 255],
        intensity: 2.0,
        position: [-74.05, 40.7, 8000] // High above the city
      }});

      const lightingEffect = new LightingEffect({{ambientLight, pointLight}});

      // Material properties for the buildings (metallic shine)
      const material = {{
        ambient: 0.1,
        diffuse: 0.6,
        shininess: 32,
        specularColor: [60, 64, 70]
      }};

      const THEME = {{
        buildingColor: [74, 80, 87],
        trailColor0: [253, 128, 93], // Orange
        trailColor1: [23, 184, 190]  // Teal
      }};

      // 3. Initialize DeckGL
      const deckgl = new deck.DeckGL({{
        container: 'container',
        mapStyle: 'https://basemaps.cartocdn.com/gl/dark-matter-nolabels-gl-style/style.json',
        initialViewState: {{
          latitude: 40.72,
          longitude: -74.00,
          zoom: 12,
          bearing: 0,
          pitch: 45
        }},
        controller: true,
        effects: [lightingEffect] // Apply the lighting
      }});

      // 4. Animation Loop
      const LOOP_LENGTH = 1800; 
      const ANIMATION_SPEED = 30; 
      let time = 0;

      function animate() {{
        time = (Date.now() / 1000 * ANIMATION_SPEED) % LOOP_LENGTH;

        // Layer: Buildings (Extruded 3D with Material)
        const buildingsLayer = new deck.PolygonLayer({{
          id: 'buildings',
          data: BUILDINGS_DATA,
          extruded: true,
          wireframe: false,
          opacity: 0.5,
          getPolygon: d => d.polygon,
          getElevation: d => d.height,
          getFillColor: THEME.buildingColor,
          material: material 
        }});

        // Layer: Trips (Animated Glowing Lines)
        const tripsLayer = new deck.TripsLayer({{
          id: 'trips',
          data: TRIPS_DATA,
          getPath: d => d.path,
          getTimestamps: d => d.timestamps,
          getColor: d => (d.vendor === 0 ? THEME.trailColor0 : THEME.trailColor1),
          opacity: 1.0, 
          widthMinPixels: 2,
          rounded: true,
          trailLength: 180, // Shorter trail for "busy city" feel
          currentTime: time,
          shadowEnabled: false
        }});

        deckgl.setProps({{
          layers: [buildingsLayer, tripsLayer]
        }});

        requestAnimationFrame(animate);
      }}

      animate();
    </script>
  </body>
</html>
"""

# --- 3. Save to File ---
file_name = "../data/trips_theme_final.html"
with open(file_name, "w") as f:
    f.write(html_template)

print(f"Successfully generated {file_name}")

Loading trips data...
Loading buildings data...
Successfully generated ../data/trips_theme_final.html
